In [1]:
import magenta
import note_seq
import tensorflow

print('🎉 Done!')
print(magenta.__version__)
print(tensorflow.__version__)

/home/alenning/school/stats426/ArtificialRodrigo/venv/lib/python3.6/site-packages/librosa/util/decorators.py:9: NumbaDeprecationWarning: An import was requested from a module that has moved location.
Import of 'jit' requested from: 'numba.decorators', please update to use 'numba.core.decorators' or pin to Numba version 0.48.0. This alias will not be present in Numba version 0.50.0.
  from numba.decorators import jit as optional_jit
/home/alenning/school/stats426/ArtificialRodrigo/venv/lib/python3.6/site-packages/pydub/utils.py:170: RuntimeWarning: Couldn't find ffmpeg or avconv - defaulting to ffmpeg, but may not work
  warn("Couldn't find ffmpeg or avconv - defaulting to ffmpeg, but may not work", RuntimeWarning)


🎉 Done!
2.1.3
2.6.2


In [12]:
ns = note_seq.midi_file_to_note_sequence('Solo.mid')
ns

ticks_per_quarter: 480
time_signatures {
  time: 2.0
  numerator: 4
  denominator: 4
}
key_signatures {
  time: 2.0
}
tempos {
  qpm: 120.0
}
tempos {
  time: 2.0
  qpm: 138.9998957500782
}
notes {
  pitch: 61
  velocity: 51
  start_time: 2.564748625
  end_time: 2.6897487187499998
}
notes {
  pitch: 64
  velocity: 55
  start_time: 2.6996408125
  end_time: 2.83543228125
}
notes {
  pitch: 66
  velocity: 55
  start_time: 2.87859778125
  end_time: 2.96852590625
}
notes {
  pitch: 66
  velocity: 22
  start_time: 3.1510800000000003
  end_time: 3.37500103125
}
notes {
  pitch: 66
  velocity: 72
  start_time: 3.4334543125000003
  end_time: 3.57284290625
}
notes {
  pitch: 64
  velocity: 53
  start_time: 3.56564865625
  end_time: 3.66097246875
}
notes {
  pitch: 66
  velocity: 75
  start_time: 3.77967759375
  end_time: 3.8911884687500002
}
notes {
  pitch: 68
  velocity: 60
  start_time: 3.87500140625
  end_time: 4.4100737500000005
}
notes {
  pitch: 66
  velocity: 62
  start_time: 4.404678062

In [23]:
import copy

def change_tempo(note_sequence, new_tempo):
    new_sequence = copy.deepcopy(note_sequence)
    ratio = note_sequence.tempos[0].qpm / new_tempo
    for note in new_sequence.notes:
        note.start_time = note.start_time * ratio
        note.end_time = note.end_time * ratio
    new_sequence.tempos[0].qpm = new_tempo
    return new_sequence
    
ns = change_tempo(ns, new_tempo = 138.9998957500782) 

len(ns.notes)

17393

In [15]:
print('Downloading model bundle. This will take less than a minute...')
note_seq.notebook_utils.download_bundle('basic_rnn.mag', 'content/')

# Import dependencies.
from magenta.models.melody_rnn import melody_rnn_sequence_generator
from magenta.models.shared import sequence_generator_bundle
from note_seq.protobuf import generator_pb2
from note_seq.protobuf import music_pb2

# Initialize the model.
print("Initializing Melody RNN...")
bundle = sequence_generator_bundle.read_bundle_file('content/basic_rnn.mag')
generator_map = melody_rnn_sequence_generator.get_generator_map()
melody_rnn = generator_map['basic_rnn'](checkpoint=None, bundle=bundle)
melody_rnn.initialize()

print('🎉 Done!')

Initializing Melody RNN...
'model_variables' collection should be of type 'byte_list', but instead is of type 'node_list'.
INFO:tensorflow:Restoring parameters from /tmp/tmp7vxs030t/model.ckpt
🎉 Done!


In [41]:
from magenta.models.melody_rnn import melody_rnn_create_dataset

# help(melody_rnn_create_dataset)
melody_rnn_create_dataset.console_entry_point()

# seq


MelodyRnnConfigError: Exactly one of `--config` or `--melody_encoder_decoder` must be supplied.

In [20]:
# Model options. Change these to get different generated sequences! 

input_sequence = ns
num_steps = 128 # change this for shorter or longer sequences
temperature = 1.0 # the higher the temperature the more random the sequence.

# Set the start time to begin on the next step after the last note ends.
last_end_time = (max(n.end_time for n in input_sequence.notes)
                  if input_sequence.notes else 0)
qpm = input_sequence.tempos[0].qpm 
seconds_per_step = 60.0 / qpm / melody_rnn.steps_per_quarter
total_seconds = num_steps * seconds_per_step

generator_options = generator_pb2.GeneratorOptions()
generator_options.args['temperature'].float_value = temperature
generate_section = generator_options.generate_sections.add(
  start_time=last_end_time + seconds_per_step,
  end_time=total_seconds)

# Ask the model to continue the sequence.
sequence = melody_rnn.generate(input_sequence, generator_options)

note_seq.plot_sequence(sequence)
note_seq.play_sequence(sequence, synth=note_seq.fluidsynth)


EventSequenceRnnModelError: primer sequence must be shorter than `num_steps`